In [1]:
import numpy as np
from scipy.signal import remez, lfilter, stft
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from functools import reduce

Lets build some data to assess. We want both gaussian and non gaussian signals so we can assess what spectral kurtosis picks up.

In [2]:
fftsize = 128
noverlap = 64
t=10
fs=1000
tarr = np.arange(0, t, 1/fs)

# Background noise
background_noise_pwr = 1
timeseries = np.random.normal(0,np.sqrt(background_noise_pwr)/2, len(tarr)) + 1j*np.random.normal(0,np.sqrt(background_noise_pwr)/2, len(tarr))

# Signal
sine_fc = 700
timeseries += np.exp(2j*np.pi*sine_fc*tarr)

# Noisy source
noise = np.random.normal(0,np.sqrt(background_noise_pwr*32)/2, len(tarr)) + 1j*np.random.normal(0,np.sqrt(background_noise_pwr*32)/2, len(tarr))
f1=200
f2=400
BW=(f2-f1)/2
noise_fc=(f1+f2)/2
bands = [0,BW,BW+BW/6,fs/2]
taps = remez(numtaps=500, bands=bands, desired=[1,0], fs=fs)
band_limited_noise = lfilter(b=taps,a=1,x=noise)
timeseries += band_limited_noise*np.exp(2j*np.pi*noise_fc*tarr)

Now lets get a spectrogram

In [3]:
# The output of this spectrogram is the psd
freqs, times, spec = stft(x=timeseries, fs=fs, nperseg=fftsize, noverlap=noverlap, return_onesided=False)

spec=np.rot90(spec)

Plot it to see that it makes sense. We expect a noise burst and a sine wave.

In [4]:
fig = make_subplots(2,1, shared_xaxes=True, row_heights=[1,2], vertical_spacing=0)

spec_trace = go.Scatter(y=10.*np.log10(np.abs(spec[-10])), x0=0, dx=fs/fftsize, line=dict(color='black'))
spectrogram_trace = go.Heatmap(z=10.*np.log10(np.abs(spec)), x0=0, dx=fs/fftsize, y=times[::-1], colorbar=dict(title='Power [dB]'))

fig.update_layout(
    plot_bgcolor='white',
    yaxis=dict(title='Power [dB]', gridcolor='grey'),
    yaxis2=dict(autorange='reversed', title='Time [s]'),
    xaxis2=dict(scaleanchor='x', exponentformat='SI', ticksuffix='Hz')
)
fig.add_trace(spec_trace,1,1)
fig.add_trace(spectrogram_trace,2,1)

fig.show()

Ok onto spectral kurtosis. Following from the Gary/Nita paper each cell of the above PSD spectrogram is `P[m,k]` where `P` means power, `M` means sample in time domain, and `k` means frequency channel. We need to compute `S1` and `S2`.

In [5]:
S1 = np.empty_like(spec, dtype='float')
S2 = np.empty_like(S1)
M = 5 # number of time integrations to sum over

for k in np.arange(spec.shape[1]):
    for m in np.arange(0,spec.shape[0]):
        S1[m, k] = np.sum(np.abs(spec[m:m+M, k])**2)
        S2[m, k] = np.sum(np.abs(spec[m:m+M, k])**4)




SK = ((M+1)/(M-1))*(M*(S2/(S1**2))-1)

Now lets plot that to see what we see. We'll look at the original spectrogram as well as the new 'kurtogram'.

In [6]:
fig = make_subplots(1,2, horizontal_spacing=0.1, shared_yaxes=True)

kurtogram_trace = go.Heatmap(z=SK, colorbar=dict(x=1, title='kurtosis'), x0=0, dx=fs/fftsize, y=times[::-1])

fig.add_trace(spectrogram_trace,1,1)
fig.add_trace(kurtogram_trace,1,2)

fig.update_layout(
    yaxis=dict(autorange='reversed', title='Time [s]'),
    xaxis=dict(exponentformat='SI', ticksuffix='Hz'),
    xaxis2=dict(exponentformat='SI', ticksuffix='Hz')
)
fig.update_traces(colorbar=dict(x=0.45), col=1)
fig.show()

Alright looks like the sine wave is heavily "discovered" while the noise burst is not (except where it starts and stops which I think is fair?). I _did_ expect that the sine wave would have an SK value of >>1 while what I see is that the mean of the SK matrix `E(SK(entire matrix)) == 1` (good!) but that `E(SK(sine))==0` (???).

In [7]:
print(f"E(SK(entire matrix)) == {np.mean(SK)}")
print(f"E(SK(sine)) == {np.mean(SK[:,int(sine_fc/fs * fftsize)])}")


E(SK(entire matrix)) == 1.027612988055385
E(SK(sine)) == 0.09342316022592281
